In [1]:
import numpy as np
import pandas as pd
import math as m
import matplotlib.pyplot as plt
import warnings
import scipy
from sklearn.decomposition import PCA


from visuals import *
from my_lib import *

In [2]:
warnings.simplefilter('ignore')

plt.rcParams['figure.figsize'] = 5, 5
plt.rcParams['font.family'] = 'DejaVu Serif'
plt.rcParams['lines.linewidth'] = 2
plt.rcParams['lines.markersize'] = 8
plt.rcParams['xtick.labelsize'] = 16
plt.rcParams['ytick.labelsize'] = 16
plt.rcParams['legend.fontsize'] = 16
plt.rcParams['axes.titlesize'] = 24
plt.rcParams['axes.labelsize'] = 8

In [3]:
def CartesianToSpherical(point):
    r = np.sqrt(sum(point ** 2))
    n = len(point)
    phi = np.zeros(n - 1)
    
    for i in range(n - 2):
        phi[i] = np.arccos(point[i] / np.sqrt(sum(point[i:] ** 2)))
        
    if point[-1] >= 0:
        phi[n - 2] = np.arccos(point[n - 2] / np.sqrt(point[n - 1] ** 2 + point[n - 2] ** 2))
    else:
        phi[n - 2] = 2 * np.pi - np.arccos(point[n - 2] / np.sqrt(point[n - 1] ** 2 + point[n - 2] ** 2))
        
    return np.hstack((phi, r))


def TrajectoryToSpherical(tr):
    tr_spherical = np.zeros(tr.shape)
    for i, point in enumerate(tr):
        tr_spherical[i] = CartesianToSpherical(point)
    return tr_spherical


def SphericalToCartesian(point):
    phi, r = point[:-1], point[-1]
    n = len(point)
    x = np.zeros(n) 
    cur = r
    
    for i in range(n - 1):
        x[i] = cur * np.cos(phi[i])
        cur *= np.sin(phi[i])

    x[n - 1] = cur
    return x
    

def TrajectoryToCartesian(tr):
    tr_cartesian = np.zeros(tr.shape)
    for i, point in enumerate(tr):
        tr_cartesian[i] = SphericalToCartesian(point)
    return tr_cartesian

In [4]:
def orientation(point, n, point0, dist=False):
    ans = 0
    for i in range(len(n)):
        ans += n[i]*(point[i] - point0[i])
    if dist:
        return ans/(np.sum(n**2))**.5
        
    else:
        return np.sign(ans)

def HankelMatrix(X, L):  
    N = X.shape[0]
    return scipy.linalg.hankel(X[ : N - L + 1], X[N - L : N])

def prepare_time_series(_dir, centred = True):
    data = pd.read_csv(_dir, delimiter =';', decimal=',')
    
    frequency = len(data)/(data['time'].values[-1]-data['time'].values[0])
    
    assert 490 < frequency < 510, f'Bad frequency {frequency}'

    _x = ( (data['X_value'].values)**2 + (data['Y_value'].values)**2 + (data['Z_value'].values)**2)**.5
    
    if centred:
        _m = np.mean(_x)
        _x = (_x-_m)
        
    _t = (data['time'].values).astype(float).reshape([-1,])

    _t = np.linspace(0,_t[-1]-_t[0],len(_x))
        
    return _x,_t

# Алгоритм с использованием средней фазовой траетории

In [5]:
x_acc_test, t_test = prepare_time_series('./data/30 sec 2_accm.csv')

x_acc, t = prepare_time_series('./data/long_walk_100_acc.csv')

dt = 450*20
x_acc = x_acc[7007:7007+dt]
fig = go.Figure()
fig.add_scatter(y = x_acc, mode='lines', name='x_acc')
fig.show()

In [6]:
x_acc_test_ = x_acc_test[:25000]*0.8

In [7]:
modif = np.concatenate([np.ones(3000),
                        np.linspace(1,0,500),
                        np.zeros(1500)+.2,
                        np.linspace(0,1,1000),
                        np.ones(6000),
                        np.linspace(1,0,400),
                        np.zeros(4000)+.2,
                        np.linspace(0,1,1000)],
                        axis = 0)

In [8]:
modif = np.concatenate([modif,
                       np.ones(len(x_acc_test_)-len(modif))],
                       axis = 0)

In [9]:
x_acc_test_m = x_acc_test_ *0.8 * modif
fig = go.Figure()
fig.add_scatter(y = x_acc_test_m, mode='lines', name='x_acc')
fig.show()

In [61]:
X = HankelMatrix(x_acc,500)
X_test = HankelMatrix(x_acc_test_m,500)

pca = PCA(n_components = 10)
X_PCA = pca.fit_transform(X)
X_PCA_test = pca.transform(X_test)

In [147]:
####################################################
X_mean = X_PCA[:460]
for i in range(1,18):
    X_mean += X_PCA[460*i:460*(i+1)]
X_mean /= 18

####################################################
X_std = (X_PCA[:460] - X_mean)**2
for i in range(1,18):
    X_std += (X_PCA[460*i:460*(i+1)] - X_mean)**2
X_std = (X_std/18)**.5

D = 3*X_std.mean()

In [63]:
phase_index = 667-500
Point_zero_phase = X_PCA[phase_index]
Point_half_phase = X_PCA[phase_index + 230]

In [64]:
a = X_PCA[phase_index+1]
b = X_PCA[phase_index-1]
n = (b-a)

In [65]:
r = np.array([a + 0*(b-a)])

for t_param in np.linspace(-50,50,200):
    
    _r = np.array([a + t_param*(b-a)])
    
    r = np.concatenate([r,_r], axis = 0)

In [66]:
indexes = []
for i in range(1,len(X_PCA_test)):
    if (np.sum((Point_zero_phase - X_PCA_test[i])**2))**.5 <= D:
        if orientation(X_PCA_test[i-1],n, Point_zero_phase) != orientation(X_PCA_test[i],n, Point_zero_phase):
            indexes.append(i)
indexes = np.array(indexes)

In [67]:
fig = go.Figure()

fig.update_layout( autosize=False, width=950, height=500)

fig.add_scatter(y = x_acc_test_m,x = np.arange(len(x_acc_test_m)), mode='lines', name='X_PCA',opacity=0.5)

indexes_init = indexes + 500
fig.add_scatter(y = x_acc_test_m[indexes_init],
                x = indexes_init, 
                mode='markers',
                marker_size=10)

fig.show()

### Без ограничения на дисперсию

In [68]:
indexes = []
for i in range(1,len(X_PCA)):
    if (np.sum((Point_zero_phase - X_PCA[i])**2))**.5 <= np.inf:
        if orientation(X_PCA[i-1],n, Point_zero_phase) != orientation(X_PCA[i],n, Point_zero_phase):
            indexes.append(i)
indexes = np.array(indexes)

In [69]:
fig = go.Figure()

fig.update_layout( autosize=False, width=950, height=500)

fig.add_scatter(y = x_acc,x = np.arange(len(x_acc)), mode='lines', name='X_PCA',opacity=0.5)

indexes_init = indexes + 500
fig.add_scatter(y = x_acc[indexes_init],
                x = indexes_init, 
                mode='markers',
                marker_size=10)

fig.show()

In [ ]:
if X_PCA.shape[1] ==3:
    p_1, p_2 = np.mgrid[0:np.pi:100j, 0:2*np.pi:100j]

    x_s = Point_zero_phase[0] + D*np.sin(p_1)*np.cos(p_2)
    y_s = Point_zero_phase[1] + D*np.sin(p_1)*np.sin(p_2)
    z_s = Point_zero_phase[2] + D*np.cos(p_1)

    fig_2 = go.Figure()
    fig_2.update_layout(autosize=False, width=1000, height=1000)

    fig_2.add_trace(go.Scatter3d(x=X_PCA[:,0],
                                 y=X_PCA[:,1],
                                 z=X_PCA[:,2],
                                 marker=dict(size=0.1,line=dict(width=0.01)),
                                 name = False
                                )
                    )

    fig_2.add_trace(go.Scatter3d(x=X_mean[:,0],
                                 y=X_mean[:,1],
                                 z=X_mean[:,2],
                                 marker=dict(size=0.1,line=dict(width=0.01)),
                                )
                    )

    fig_2.add_trace(go.Surface(x=x_s,
                               y=y_s,
                               z=z_s,
                               showscale=False,
                               opacity=0.2,
                               surfacecolor = np.linspace(0,100,len(x_s))))

    fig_2.add_trace(go.Scatter3d(x=X_PCA_test[:,0],
                                 y=X_PCA_test[:,1],
                                 z=X_PCA_test[:,2],
                                 marker=dict(size=0.1,line=dict(width=0.01)),
                                )
                    )

    fig_2.add_trace(go.Scatter3d(x=[Point_zero_phase[0]],
                               y=[Point_zero_phase[1]],
                               z=[Point_zero_phase[2]],
                               mode='markers',
                               marker_size=10,
                               marker_color='rgba(10, 250, 250, .7)',
                               name='Zero point'))

    fig_2.add_trace(go.Scatter3d(x=[Point_half_phase[0]],
                               y=[Point_half_phase[1]],
                               z=[Point_half_phase[2]],
                               mode='markers',
                               marker_size=10,
                               marker_color='rgba(10, 250, 250, .7)',
                               name='Half point'))

    fig_2.add_trace(go.Scatter3d(x=r[:,0],
                               y=r[:,1],
                               z=r[:,2],
                               marker=dict(size=0.1,line=dict(width=0.1))))


    fig_2.layout.template = 'plotly_white'
    fig_2.show()

# Алгоритм на чистых данных (модификация Мотренко)

In [48]:
x_acc, t = prepare_time_series('./data/long_walk_100_acc.csv')
dt = 450*20
x_acc = x_acc[7007:7007+dt]

In [49]:
X = HankelMatrix(x_acc,500)
pca = PCA(n_components = 3)
X_PCA = pca.fit_transform(X)
fig = go.Figure()
fig.add_scatter(y = x_acc, mode='lines', name='x_acc')
fig.show()

In [154]:
X = HankelMatrix(x_acc,500)
pca = PCA(n_components = 5)
X_PCA = pca.fit_transform(X)

In [155]:
#точка на фазовой траектории
index_0 = 667-500
phi_0 = X_PCA[index_0]

#направляющий вектор прямой из центра в точку фазовой траектории
n_ph = phi_0 - 0

In [156]:
#находим направляющий вектор для касательной и точку для проекции на этой прямой
a = X_PCA[index_0+1]
b = X_PCA[index_0-1]
n = (b-a)
point_for_projection = a + n*(-10)

In [157]:
# Находим плоскоть перпендикулярную прямой из центра и проходящуую через point_for_projection
# Получем уравнение вида n_ph[0]*(x[0] - point_for_projection[0]) + ... = 0
# Получем уравнение прямой из центра координат в параметрической (относительно параметра t) виде
#         x[0] = 0 + n_ph[0] * t
# Подставляем в уравнение  плоскости n_ph[0]*(n_ph[0]*t - point_for_projection[0]) + ... = 0
# Находим t 
t = np.sum(n_ph * point_for_projection)/np.sum(n_ph**2)

projection_point = n_ph * t

In [158]:
# Проверка на 3мерном случае 
if X_PCA.shape[1] ==3:
    fig_2 = go.Figure()
    fig_2.update_layout(autosize=False, width=800, height=800)
    fig_2.add_trace(go.Scatter3d(x=X_PCA[:,0],
                                 y=X_PCA[:,1],
                                 z=X_PCA[:,2],
                                 marker=dict(size=0.1,line=dict(width=0.01)),
                                 name = False))
    fig_2.add_trace(go.Scatter3d(x=[projection_point[0]],
                               y=[projection_point[1]],
                               z=[projection_point[2]],
                               mode='markers',
                               marker_size=10,
                               marker_color='rgba(10, 250, 250, .7)',
                               name='projection_point'))
    fig_2.layout.template = 'plotly_white'
    fig_2.show()

In [168]:
# получем ветор нормальи для итоговой плоскости
n_final = projection_point - point_for_projection
# Предел по расстоянию (ближе чем середина между максимальный расстоянием между 2мя точакми на таректории)
limit = np.sum((np.max(X_PCA,axis = 0) - np.min(X_PCA,axis = 0))**2)**.5/2

In [173]:
####################################################
X_mean = X_PCA[:460]
for i in range(1,18):
    X_mean += X_PCA[460*i:460*(i+1)]
X_mean /= 18

####################################################
X_std = (X_PCA[:460] - X_mean)**2
for i in range(1,18):
    X_std += (X_PCA[460*i:460*(i+1)] - X_mean)**2
X_std = (X_std/18)**.5

D = 3*X_std.mean()

In [174]:
print(f"D:{np.round(D,3)}, Limit:{np.round(limit,3)}")

D:32.56, Limit:162.853


In [175]:
indexes = []
for i in range(1,len(X_PCA)):
    if np.sum((phi_0 - X_PCA[i])**2)**.5 <= limit:
        if orientation(X_PCA[i-1],n_final, np.zeros(len(phi_0))) != orientation(X_PCA[i],n_final, np.zeros(len(phi_0))):
            indexes.append(i)
indexes = np.array(indexes[:-1])

In [176]:
indexes

array([ 170,  397,  623,  847, 1080, 1304, 1369, 1376, 1539, 1571, 1576,
       1765, 1828, 1835, 2002, 2228, 2464, 2687, 2925, 3149, 3389, 3614,
       3684, 3691, 3853, 4082, 4138, 4147, 4311, 4539, 4770, 4993, 5057,
       5063, 5233, 5458, 5516, 5528, 5694, 5922, 5981, 5988, 6155, 6382,
       6442, 6455, 6617, 6846, 6903, 6919, 7082, 7313, 7363, 7384, 7547,
       7774, 7826, 7847, 8006, 8232, 8282, 8307, 8467])

In [177]:
fig = go.Figure()

fig.update_layout( autosize=False, width=950, height=500)
fig.add_scatter(y = x_acc,
                x = np.arange(len(x_acc)),
                mode='lines',
                name='X_PCA',
                opacity=0.5)
indexes_init = indexes + 500
fig.add_scatter(y = x_acc[indexes_init],
                x = indexes_init, 
                mode='markers',
                marker_size=10)
fig.show()